# 02 - Data from the Web

## Part 0 - Helpers and constants

#### Import modules

In [56]:
# Import necessary modules
import requests
from bs4 import BeautifulSoup
import re

#### Constants

In [57]:
# Base URL for isa.epfl.ch public report searches
isa_base_url = 'http://isa.epfl.ch/imoniteur_ISAP/'

#### Helpers

In [58]:
# Helper for creating search path
def isa_url(path):
    return isa_base_url + path

In [59]:
# Allow accessing dictionary items as object attributes
# https://goodcode.io/articles/python-dict-object/
class objdict(dict):
    def __getattr__(self, name):
        if name in self:
            return self[name]
        else:
            raise AttributeError("No such attribute: " + name)

    def __setattr__(self, name, value):
        self[name] = value

    def __delattr__(self, name):
        if name in self:
            del self[name]
        else:
            raise AttributeError("No such attribute: " + name)

In [60]:
# Fetch the given url using a GET requests with the supplied parameters
def get_page(url, params=None):
    r = requests.get(url, params)
    
     # Check whether the request succeeded or not
    if r.status_code is not requests.codes.ok:
        print("Something went wrong. Got status code = " + str(r.status_code))
        return None
    
    # TODO: Check Content-Length
    
    # Extract the response body
    html = r.text
    
    # Parse it with BeautifulSoup
    return BeautifulSoup(html, 'html.parser')

## Part 1 - Scraper Module

The first step is to fetch all the data from ISA.

To do this, we will have to scrape the respective frames that ISA serves for the form and then the search results. Steps are detailed below.

In [61]:
# URL of the public ISA home page.
isa_home_url = isa_url('%21gedpublicreports.htm?ww_i_reportmodel=133685247')

#### Get the form URL from the home page

In [6]:
home_soup = get_page(isa_home_url)

In [62]:
# Find the form frame
toc_frame = home_soup.find('frame', attrs={'name': 'toc'})

In [63]:
# Extract the form's URL
toc_frame_url = toc_frame.attrs['src']
toc_frame_url # Sanity check

'!GEDPUBLICREPORTS.filter?ww_i_reportModel=133685247'

In [64]:
# Repeat previous process for the form's frame
toc_url = isa_url(toc_frame_url)

#### Get the form

In [10]:
toc_soup = get_page(toc_url)

In [65]:
# Find the form itself within the page
# The form's name is a heuristic, read from the page's source
form_elem = toc_soup.find('form', attrs={'name': 'f'})

In [66]:
# Find the form's action on validation
form_action = form_elem['action']
form_action_url = isa_url(form_action)
form_action_url # Debug print

'http://isa.epfl.ch/imoniteur_ISAP/!GEDPUBLICREPORTS.filter'

In [67]:
# Define a payload dictionary with all the parameters expected by ISA's API endpoint

# /!\ By default we will request all possibilities from the endpoint, and then filter. /!\ #

# Example requests for specific academic or pedagogic periods are left FYI.

payload = {
    'ww_b_list': '1',
    'ww_i_reportmodel': '133685247',
    'ww_c_langue': '',
    
    # Format = html
    'ww_i_reportModelXsl': '133685270', 
    
    # Faculty = { Informatique : 249847 }
    'zz_x_UNITE_ACAD': 'Informatique',
    'ww_x_UNITE_ACAD': '249847',
    
    # Academic Period = { '' : null } if we want all possible periods
    #                 = { '2016-2017' : 355925344 } for a specific year
    'zz_x_PERIODE_ACAD': '',
    'ww_x_PERIODE_ACAD': 'null',

    
    # Pedagogic Period = { '' : null } if we want all possible periods
    #                  = { 'Bachelor semestre 1' : 249108 } for a specific period
    'zz_x_PERIODE_PEDAGO': '',
    'ww_x_PERIODE_PEDAGO': 'null',
    
    # Winter or summer semesters
    'zz_x_HIVERETE': '',
    'ww_x_HIVERETE': 'null',
    
    'dummy': 'ok'
}

#### Fill in the form and parse the search results

In [68]:
# Parse the result
form_result_soup = get_page(form_action_url, params=payload)
# form_result_soup.prettify() # Debug print

In [69]:
# Extract the links from the list of results
all_links = form_result_soup('a', class_='ww_x_GPS')
# all_links # Debug print

In [70]:
# Store the links in a dictionary. Some cleaning is applied, such as whitespace stripping
# Note : removing 'Tous' allows us to iterate and filter independently each result
#        instead of an aggregate HTML table which would be much more painful to parse
links = [
    objdict({
        'text': link.text.strip(),
        'url': link.attrs['onclick']
    }) for link in all_links if link.text.strip() != 'Tous'
]

For each link,the page loads the respective results with the following on-click action :

```
loadReport('ww_x_GPS=2021043255');return false;
```

We will use the following function ```parse_url()``` to extract the ```ww_x_GPS``` parameter expected by the API to return the desired information about the students.

In [71]:
parse_url_pattern = r"""'(\w+)=(\d+)'"""
parse_url_re = re.compile(parse_url_pattern)

def parse_url(url):
    match = re.search(parse_url_pattern, url)

    if match == None:
        print('parse_url: parsing failure: %s' % url)
        return None
    
    return objdict({
        'key': match.group(1),
        'value': match.group(2)
    })

The list itself must be parsed to extract information regarding section, academic year, pedagogic period. The format is the following :

```
Informatique, 2016-2017, Bachelor semestre 1
```

We call an element of the list an item, and it will be parsed by the following ```parse_item()``` function.

In [72]:
parse_item_pattern = r"""Informatique,\s*(?P<start_year>\d+)-(?P<end_year>\d+),\s*(?P<degree>[\w]+) semestre (?P<semester>\d)"""
parse_item_re = re.compile(parse_item_pattern)

def parse_item(item, url, payload):
    match = re.match(parse_item_re, item)
    
    # The above regex will match only the kind of records we are interested in, so we can
    # safely drop all the non-matching ones
    if match == None:
        # print('Match failed: %s ' % item)
        return None
    
    parsed_url = parse_url(url)
    
    if parsed_url == None:
        return None
    
    params = payload.copy()
    params[parsed_url.key] = parsed_url.value
    
    return objdict({
        'start_year': int(match.group('start_year')),
        'end_year': int(match.group('end_year')),
        'degree': match.group('degree'),
        'semester': int(match.group('semester')),
        'params': params
    })

# Filter all None elements from the given list
def filter_none(a_list):
    return [item for item in a_list if item != None]

In [73]:
all_items = [parse_item(link.text, link.url, payload) for link in links]

In [590]:
def is_valid_item(item):
    return item != None and item.start_year >= 2007

def filter_items(items):
    return [item for item in items if is_valid_item(item)]

In [591]:
items = filter_items(all_items)
items

[{'degree': 'Bachelor',
  'end_year': 2008,
  'params': {'dummy': 'ok',
   'ww_b_list': '1',
   'ww_c_langue': '',
   'ww_i_reportModelXsl': '133685270',
   'ww_i_reportmodel': '133685247',
   'ww_x_GPS': '71297531',
   'ww_x_HIVERETE': 'null',
   'ww_x_PERIODE_ACAD': 'null',
   'ww_x_PERIODE_PEDAGO': 'null',
   'ww_x_UNITE_ACAD': '249847',
   'zz_x_HIVERETE': '',
   'zz_x_PERIODE_ACAD': '',
   'zz_x_PERIODE_PEDAGO': '',
   'zz_x_UNITE_ACAD': 'Informatique'},
  'semester': 1,
  'start_year': 2007},
 {'degree': 'Bachelor',
  'end_year': 2008,
  'params': {'dummy': 'ok',
   'ww_b_list': '1',
   'ww_c_langue': '',
   'ww_i_reportModelXsl': '133685270',
   'ww_i_reportmodel': '133685247',
   'ww_x_GPS': '71297550',
   'ww_x_HIVERETE': 'null',
   'ww_x_PERIODE_ACAD': 'null',
   'ww_x_PERIODE_PEDAGO': 'null',
   'ww_x_UNITE_ACAD': '249847',
   'zz_x_HIVERETE': '',
   'zz_x_PERIODE_ACAD': '',
   'zz_x_PERIODE_PEDAGO': '',
   'zz_x_UNITE_ACAD': 'Informatique'},
  'semester': 2,
  'start_year':

#### Going through the years to extract the list of enrolled students

In [ ]:
list_page_url = isa_url('!GEDPUBLICREPORTS.html')

def parse_student_row(tr, item, headers):
    tds = tr.find_all('td')
    texts = [td.text for td in tds]
    
    res = {}
    for i, header in enumerate(headers):
        res[header] = texts[i]
    
    item_keys = ['degree', 'semester', 'start_year', 'end_year']
    for key in item_keys:
        res[key] = item[key]
    
    return objdict(res)

def parse_students_list(page_soup, item):
    table = page_soup.find('table')
    trs = table.find_all('tr')
    
    print(item)
    print(trs)
    
    (header_row, students_rows) = (trs[1], trs[2:])
        
    headers = [x.text for x in header_row.find_all('th')]
    
    return [
        parse_student_row(student_row, item, headers) for student_row in students_rows
    ]

def load_student_page(item):
    return objdict({
        'soup': get_page(list_page_url, item.params),
        'item': item
    })

students_pages = [load_student_page(item) for item in items]

students_lists = [
    parse_students_list(page.soup, page.item) for page in students_pages
]

{'params': {'ww_i_reportmodel': '133685247', 'ww_x_PERIODE_PEDAGO': 'null', 'ww_c_langue': '', 'zz_x_PERIODE_PEDAGO': '', 'zz_x_UNITE_ACAD': 'Informatique', 'ww_x_GPS': '71297531', 'zz_x_HIVERETE': '', 'ww_x_PERIODE_ACAD': 'null', 'ww_x_HIVERETE': 'null', 'ww_x_UNITE_ACAD': '249847', 'ww_i_reportModelXsl': '133685270', 'zz_x_PERIODE_ACAD': '', 'ww_b_list': '1', 'dummy': 'ok'}, 'start_year': 2007, 'end_year': 2008, 'semester': 1, 'degree': 'Bachelor'}
[<tr><th colspan="12"><font color="black">Informatique, 2007-2008, Bachelor semestre 1</font>
 (90 ét.)
    </th></tr>, <tr><th>Civilité</th><th>Nom Prénom</th><th>Orientation Bachelor</th><th>Orientation Master</th><th>Spécialisation</th><th>Filière opt.</th><th>Mineur</th><th>Statut</th><th>Type Echange</th><th>Ecole Echange</th><th>No Sciper</th></tr>, <tr><td style="white-space:nowrap">Monsieur</td><td style="white-space:nowrap">Arévalo Christian</td><td style="white-space:nowrap"></td><td style="white-space:nowrap"></td><td style="whi

In [ ]:
def flatten_list(a_list):
    return [item for sublist in a_list for item in sublist]

student_list = flatten_list(students_lists)

In [ ]:
import pandas as pd

In [558]:
students_data = pd.DataFrame(student_list)

def load_bsc_data(data):
    bsc_data = students_data[['No Sciper', 'Civilité', 'Nom Prénom', 'degree', 'semester', 'start_year', 'end_year']]
    return bsc_data.rename(columns={'No Sciper': 'sciper', 'Civilité': 'title', 'Nom Prénom': 'name'})
    
bsc_data = load_bsc_data(students_data)

In [559]:
def filter_bsc_students(bsc_data):
    bsc_data = bsc_data[bsc_data['degree'] == 'Bachelor']
    idx1 = set(bsc_students[bsc_students['semester'] == 1].set_index('sciper').index)
    idx6 = set(bsc_students[bsc_students['semester'] == 6].set_index('sciper').index)

    idx = idx1.intersection(idx6)

    return bsc_students[bsc_students['sciper'].isin(idx)].set_index('sciper').sort_index()

bsc = filter_bsc_students(bsc_data)
bsc

title                                  name    degree  semester  \
sciper                                                                       
147008  Monsieur                           Good Xavier  Bachelor         3   
147008  Monsieur                           Good Xavier  Bachelor         2   
147008  Monsieur                           Good Xavier  Bachelor         6   
147008  Monsieur                           Good Xavier  Bachelor         5   
147008  Monsieur                           Good Xavier  Bachelor         1   
147008  Monsieur                           Good Xavier  Bachelor         4   
169569  Monsieur                     Arévalo Christian  Bachelor         3   
169569  Monsieur                     Arévalo Christian  Bachelor         4   
169569  Monsieur                     Arévalo Christian  Bachelor         5   
169569  Monsieur                     Arévalo Christian  Bachelor         2   
169569  Monsieur                     Arévalo Christian  Bachelor         6   
169569  Monsieur                     Arévalo Christian  Bachelor         1   
169731  Monsieur                        Knecht Mathieu  Bachelor         3   
169731  Monsieur                        Knecht Mathieu  Bachelor         5   
169731  Monsieur                        Knecht Mathieu  Bachelor         2   
169731  Monsieur                        Knecht Mathieu  Bachelor         6   
169731  Monsieur                        Knecht Mathieu  Bachelor         4   
169731  Monsieur                        Knecht Mathieu  Bachelor         1   
169731  Monsieur                        Knecht Mathieu  Bachelor         4   
169731  Monsieur                        Knecht Mathieu  Bachelor         3   
169795  Monsieur                       Scheiben Pascal  Bachelor         6   
169795  Monsieur                       Scheiben Pascal  Bachelor         5   
169795  Monsieur                       Scheiben Pascal  Bachelor         5   
169795  Monsieur                       Scheiben Pascal  Bachelor         3   
169795  Monsieur                       Scheiben Pascal  Bachelor         6   
169795  Monsieur                       Scheiben Pascal  Bachelor         5   
169795  Monsieur                       Scheiben Pascal  Bachelor         4   
169795  Monsieur                       Scheiben Pascal  Bachelor         1   
169795  Monsieur                       Scheiben Pascal  Bachelor         2   
171195  Monsieur                        Richter Arnaud  Bachelor         5   
...          ...                                   ...       ...       ...   
238150  Monsieur                          Poma Florian  Bachelor         6   
238150  Monsieur                          Poma Florian  Bachelor         3   
238150  Monsieur                          Poma Florian  Bachelor         2   
238150  Monsieur                          Poma Florian  Bachelor         1   
238150  Monsieur                          Poma Florian  Bachelor         5   
238150  Monsieur                          Poma Florian  Bachelor         4   
239124  Monsieur                       Tâche Guillaume  Bachelor         1   
239124  Monsieur                       Tâche Guillaume  Bachelor         5   
239124  Monsieur                       Tâche Guillaume  Bachelor         2   
239124  Monsieur                       Tâche Guillaume  Bachelor         4   
239124  Monsieur                       Tâche Guillaume  Bachelor         3   
239124  Monsieur                       Tâche Guillaume  Bachelor         6   
239170  Monsieur                       Chevalley Alain  Bachelor         6   
239170  Monsieur                       Chevalley Alain  Bachelor         3   
239170  Monsieur                       Chevalley Alain  Bachelor         5   
239170  Monsieur                       Chevalley Alain  Bachelor         1   
239170  Monsieur                       Chevalley Alain  Bachelor         4   
239170  Monsieur                       Chevalley Alain  Bachelor         2   
239314  Monsieur                 

In [560]:
def add_semesters_count(bsc):
    cols = ['sciper', 'semester']
    semester_count = bsc.reset_index()[cols].groupby('sciper').count().rename(columns={'semester': 'semester_count'})
    return bsc.merge(semester_count, left_index=True, right_index=True)
    
with_counts = add_semesters_count(bsc)
with_counts.head(20)

title               name    degree  semester  start_year  end_year  \
sciper                                                                          
147008  Monsieur        Good Xavier  Bachelor         3        2009      2010   
147008  Monsieur        Good Xavier  Bachelor         2        2008      2009   
147008  Monsieur        Good Xavier  Bachelor         6        2010      2011   
147008  Monsieur        Good Xavier  Bachelor         5        2010      2011   
147008  Monsieur        Good Xavier  Bachelor         1        2008      2009   
147008  Monsieur        Good Xavier  Bachelor         4        2009      2010   
169569  Monsieur  Arévalo Christian  Bachelor         3        2008      2009   
169569  Monsieur  Arévalo Christian  Bachelor         4        2008      2009   
169569  Monsieur  Arévalo Christian  Bachelor         5        2009      2010   
169569  Monsieur  Arévalo Christian  Bachelor         2        2007      2008   
169569  Monsieur  Arévalo Christian  Bachelor         6        2009      2010   
169569  Monsieur  Arévalo Christian  Bachelor         1        2007      2008   
169731  Monsieur     Knecht Mathieu  Bachelor         3        2008      2009   
169731  Monsieur     Knecht Mathieu  Bachelor         5        2010      2011   
169731  Monsieur     Knecht Mathieu  Bachelor         2        2007      2008   
169731  Monsieur     Knecht Mathieu  Bachelor         6        2010      2011   
169731  Monsieur     Knecht Mathieu  Bachelor         4        2009      2010   
169731  Monsieur     Knecht Mathieu  Bachelor         1        2007      2008   
169731  Monsieur     Knecht Mathieu  Bachelor         4        2008      2009   
169731  Monsieur     Knecht Mathieu  Bachelor         3        2009      2010   

        semester_count  
sciper                  
147008               6  
147008               6  
147008               6  
147008               6  
147008               6  
147008               6  
169569               6  
169569               6  
169569               6  
169569               6  
169569               6  
169569               6  
169731               8  
169731               8  
169731               8  
169731               8  
169731               8  
169731               8  
169731               8  
169731               8

In [561]:
abc = with_count[['title', 'name', 'semester_count']].reset_index().groupby('sciper').agg('first')
abc.sample(10)

title                          name  semester_count
sciper                                                        
228275  Monsieur           Garin Arnaud Michel               8
192757    Madame             Balmau Oana Maria               6
192870  Monsieur         Zablotchi Mihail Igor               6
201034  Monsieur        Kashani-Akhavan Sahand               8
201568  Monsieur  Link Jonathan Stéphane Oskar               9
185959  Monsieur                Droxler Thomas               8
238020  Monsieur    Charoud-Got Perséas Orféas               6
227775  Monsieur         Wirz Leonardo Enrique               8
205653  Monsieur           Engels Damien Lyall               6
169795  Monsieur               Scheiben Pascal               9

In [562]:
by_title = abc.groupby('title')
by_title['semester_count'].describe()

title          
Madame    count     28.000000
          mean       6.642857
          std        1.129218
          min        6.000000
          25%        6.000000
          50%        6.000000
          75%        7.250000
          max       10.000000
Monsieur  count    347.000000
          mean       7.103746
          std        1.507462
          min        4.000000
          25%        6.000000
          50%        6.000000
          75%        8.000000
          max       12.000000
Name: semester_count, dtype: float64

In [585]:
def load_msc_data(data):
    cols = [
        'Civilité', 'No Sciper', 'Nom Prénom', 'Statut',
        'Spécialisation', 'Mineur',
        'degree', 'semester', 'end_year', 'start_year'
    ]
    rename = {
        'Civilité': 'title',
        'No Sciper': 'sciper',
        'Nom Prénom': 'name',
        'Statut': 'status',
        'Spécialisation': 'specialisation',
        'Mineur': 'minor'
    }
    
    return students_data[cols].rename(columns=rename)
    
msc_data = load_msc_data(students_data)

def filter_msc_students(students_data):
    return students_data[(students_data['degree'] == 'Master') & (students_data['status'] == 'Présent')]

msc = filter_msc_students(msc_data).set_index('sciper').sort_index()
msc

title                               name   status  \
sciper                                                         
128911  Monsieur                     Gulati Asheesh  Présent   
128911  Monsieur                     Gulati Asheesh  Présent   
129093  Monsieur                         Zhou Maoan  Présent   
129326  Monsieur                     Ni Zhong Zhong  Présent   
129326  Monsieur                     Ni Zhong Zhong  Présent   
138088  Monsieur            Droz-dit-Busset Arnault  Présent   
145546  Monsieur               Clivaz Jean-Philippe  Présent   
145957  Monsieur                      Hügli Michael  Présent   
146330  Monsieur                   Cardinaux Damien  Présent   
146330  Monsieur                   Cardinaux Damien  Présent   
146330  Monsieur                   Cardinaux Damien  Présent   
146441    Madame                   Henriot Laetitia  Présent   
146742  Monsieur                       Marx Clément  Présent   
146742  Monsieur                       Marx Clément  Présent   
146742  Monsieur                       Marx Clément  Présent   
146742  Monsieur                       Marx Clément  Présent   
146742  Monsieur                       Marx Clément  Présent   
146752  Monsieur                   De Lamarter Erik  Présent   
146929  Monsieur                      Junod Antoine  Présent   
146929  Monsieur                      Junod Antoine  Présent   
147008  Monsieur                        Good Xavier  Présent   
147008  Monsieur                        Good Xavier  Présent   
147008  Monsieur                        Good Xavier  Présent   
147358  Monsieur                    Conus Christian  Présent   
147362  Monsieur               Rey Charles François  Présent   
147366  Monsieur                  Schönmann Patrick  Présent   
147445  Monsieur                Robert Pierre-Alain  Présent   
148900  Monsieur               Nansi Fabrice Cédric  Présent   
152232  Monsieur                 Anagnostaras David  Présent   
152232  Monsieur                 Anagnostaras David  Présent   
...          ...                                ...      ...   
256722  Monsieur                       Qureshi Zaid  Présent   
256722  Monsieur                       Qureshi Zaid  Présent   
256846  Monsieur        Tallec Corentin Jean Daniel  Présent   
256846  Monsieur        Tallec Corentin Jean Daniel  Présent   
256870    Madame                          Zhou Lisa  Présent   
256870    Madame                          Zhou Lisa  Présent   
257819  Monsieur              Demotz Vincent Daniel  Présent   
257819  Monsieur              Demotz Vincent Daniel  Présent   
257825  Monsieur        Alnasser Riyadh Abdulaziz M  Présent   
257825  Monsieur        Alnasser Riyadh Abdulaziz M  Présent   
259719    Madame                         Hou Yumeng  Présent   
259719    Madame                         Hou Yumeng  Présent   
259745    Madame                 Radovanovic Nevena  Présent   
259745    Madame                 Radovanovic Nevena  Présent   
259766  Monsieur       Dubedat Philippe Pierre-Elie  Présent   
259766  Monsieur       Dubedat Philippe Pierre-Elie  Présent   
259910  Monsieur         Rousseau Adrien Jean-Louis  Présent   
259910  Monsieur         Rousseau Adrien Jean-Louis  Présent   
260636  Monsieur                    Fokeas Sotirios  Présent   
260636  Monsieur                    Fokeas Sotirios  Présent   
260806  Monsieur  Rouault Sébastien Louis Alexandre  Présent   
260806  Monsieur  Rouault Sébastien Louis Alexandre  Présent   
260811  Monsieur                  Loiseleur Thibaut  Présent   
260811  Monsieur                  Loiseleur Thibaut  Présent   
260968    Madame                  Kabil Selen Hande  Présent   
260968    Madame                  Kabil Selen Hande  Présent   
261006    Madame                     M'Hamdi Meryem  Présent   
261006    Madame                     M'Hamdi Meryem  Présent   
261146  Monsieur                     Zakhour George  Présent   
261146  Monsieur                     Zakhou

In [589]:
msc_count = add_semesters_count(msc)
msc_count[(msc_count['semester_count'] < 3) & (msc_count['minor'] != '')]

title                        name   status specialisation  \
sciper                                                                 
153642  Monsieur               Imhoff Lionel  Présent                  
153645  Monsieur                Rosat Damien  Présent                  
160391  Monsieur            Chipounov Vitaly  Présent                  
172257  Monsieur              Dubut Frédéric  Présent                  
199294  Monsieur                 Jin Xuedong  Présent                  
199294  Monsieur                 Jin Xuedong  Présent                  
200419  Monsieur                   Jing Lifu  Présent                  
203301  Monsieur              Nishida Keishi  Présent                  
203301  Monsieur              Nishida Keishi  Présent                  
210271  Monsieur                Zhang Daiwei  Présent                  
210271  Monsieur                Zhang Daiwei  Présent                  
213027  Monsieur           Devillard Florent  Présent                  
216451  Monsieur            Fiszel Ruben Leo  Présent                  
216451  Monsieur            Fiszel Ruben Leo  Présent                  
225483  Monsieur  Cook Cedric Radboud Ernest  Présent                  
248358  Monsieur                   Bell Enea  Présent                  
251723  Monsieur                Korcek Juraj  Présent                  
255203  Monsieur           Kyritsis Georgios  Présent                  
255203  Monsieur           Kyritsis Georgios  Présent                  
256231  Monsieur             Fong Roger Duan  Présent                  
256612  Monsieur      Sympetheros Alexandros  Présent                  

                                                    minor  degree  semester  \
sciper                                                                        
153642  Mineur en Management, technologie et entrepren...  Master         3   
153645  Mineur en Management, technologie et entrepren...  Master         3   
160391  Mineur en Management, technologie et entrepren...  Master         3   
172257  Mineur en Management, technologie et entrepren...  Master         3   
199294  Mineur en Management, technologie et entrepren...  Master         2   
199294  Mineur en Management, technologie et entrepren...  Master         3   
200419  Mineur en Management, technologie et entrepren...  Master         2   
203301  Mineur en Management, technologie et entrepren...  Master         2   
203301  Mineur en Management, technologie et entrepren...  Master         1   
210271  Mineur en Management, technologie et entrepren...  Master         2   
210271  Mineur en Management, technologie et entrepren...  Master         1   
213027  Mineur en Management, technologie et entrepren...  Master         2   
216451                    Mineur en Ingénierie financière  Master         1   
216451                    Mineur en Ingénierie financière  Master         2   
225483  Mineur en Management, technologie et entrepren...  Master         2   
248358  Mineur en Management, technologie et entrepren...  Master         2   
251723          Mineur en Neurosciences computationnelles  Master         2   
255203                    Mineur en Ingénierie financière  Master         1   
255203                    Mineur en Ingénierie financière  Master         2   
256231                           Mineur en Microtechnique  Master         2   
256612  Mineur en Management, technologie et entrepren...  Master         2   

        end_year  start_year  semester_count  
sciper                                        
153642      2008        2007               1  
153645      2008        2007               1  
160391      2008        2007               1  
172257      2008        2007               1  
199294      2011        2010               2  
199294      2012        2011               2  
200419      2011        2010               2  
203301      2011        2010               2  
203301      2011        2010               2  
210271      2012   

In [ ]:
msc_agg = msc_count[['title', 'name', 'minor', 'semester_count']].reset_index().groupby('sciper').agg('first')
msc_agg.sample(10)